In [2]:
import pandas as pd
import numpy as np
from test_evaluate_functions.test_evaluate_functions import calculate_accuracies, test_model, variable_importance
from training_functions.training_functions import calculate_binary_variables, split, split_x_y, evaluate_models, train_ada_boost, split_easy_and_sudden_errors

# Drop nan columns:

In [48]:
dff = pd.read_csv("/home/leibniz/Desktop/IHMAN/preprocessing_results/out_lights.csv")
print("Reading done!")
# We will drop all the columns readings and lon and lat:
drop_cols = [
                col for col in dff.columns if 
                (col.startswith("power")) | (col.startswith("Active")) | (col.startswith("Reactive") | 
                (col in ["lat", "lon"])) | 
                (col == "Unnamed: 0") |
                (col.startswith("week")) |
                (col == "type") |
                (col == "ebox_id") |
                (col == "location") |
                (col == "id")
            ]
df = dff.drop(drop_cols, axis=1)
print("Drop done!")
# Interpolate with the mean in case it is necessary:
df = df.fillna(df.mean())

Reading done!
Drop done!


In [50]:
df = calculate_binary_variables(df)
# Preprocessing and split:
df["current_week"] = pd.to_datetime(df["current_week"])
train, validation, test = split(df, n_weeks=90)

cols_to_train = df.drop(["current_week", "hours_next_four_weeks", "error_next_four_weeks", "hours_week+1", "hours_week+2", "hours_week+3", "hours_week+4"], axis=1).columns
x_train, y_train = split_x_y(train, cols_to_train)
x_validation, y_validation = split_x_y(validation, cols_to_train)
x_test, y_test = split_x_y(test, cols_to_train)

0.8648401942667765
0.424756609936612
0.2965526234602259
0.2786907666031621
2014-10-06 00:00:00
2019-09-16 00:00:00
2019-09-23 00:00:00
2021-06-07 00:00:00
2021-06-14 00:00:00
2023-03-06 00:00:00


### Train model with the whole train dataset:

In [5]:
model_results = evaluate_models(
    max_depth_l = [1, 2, 3],
    n_estimators_l = [1, 2, 5, 10, 15, 20, 30],
    lr_l = [0.1, 0.2, 0.5],
    prob_threshold_l = np.arange(0.45, 0.55, 0.01).tolist(),
    x_train = x_train,
    y_train = y_train,
    x_validation = x_validation,
    y_validation = y_validation
)

/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/ensemble/_base.py:166: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/home/leibniz/Desktop/IHMAN/predictive_maintenance/training_functions/training_functions.py:162: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  model_results = model_results.append(row_to_append, ignore_index=True)
/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expec

In [6]:
model_results.loc[(model_results["yes_accuracy"] >= model_results["yes_accuracy"].max())]

learning_rate  n_estimators  total_accuracy  yes_accuracy  no_accuracy  \
495            0.1           2.0        0.962784      0.851291     0.989534   
496            0.1           2.0        0.962784      0.851291     0.989534   
497            0.1           2.0        0.962784      0.851291     0.989534   
498            0.1           2.0        0.962784      0.851291     0.989534   
499            0.1           2.0        0.962784      0.851291     0.989534   
500            0.1           2.0        0.962784      0.851291     0.989534   

     prob_threshold  tree_depth  
495            0.45         3.0  
496            0.46         3.0  
497            0.47         3.0  
498            0.48         3.0  
499            0.49         3.0  
500            0.50         3.0

In [7]:
ada_model = train_ada_boost(
    max_depth_tree = 3,
    n_estimators = 2,
    lr = 0.1,
    x  = x_train,
    y = y_train
)
# Test:
test_model(
    model = ada_model,
    x = x_test, 
    y = y_test,
    prob_threshold = 0.45
)

/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/ensemble/_base.py:166: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(


{'total_accuracy': 0.9712521683557016,
 'yes_accuracy': 0.8871287128712871,
 'no_accuracy': 0.9910088924590257}

In [8]:
# Check of the importance of the variables:
feature_importances = variable_importance(
    ada_model = ada_model, 
    trained_columns = cols_to_train
)
feature_importances.loc[feature_importances["importance"] != 0]

/home/leibniz/Desktop/IHMAN/predictive_maintenance/test_evaluate_functions/test_evaluate_functions.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  variable_importance_df = variable_importance_df.append(row_to_append, ignore_index=True)
/home/leibniz/Desktop/IHMAN/predictive_maintenance/test_evaluate_functions/test_evaluate_functions.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  variable_importance_df = variable_importance_df.append(row_to_append, ignore_index=True)
/home/leibniz/Desktop/IHMAN/predictive_maintenance/test_evaluate_functions/test_evaluate_functions.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  variable_importance_df = variable_importance_df.append(row_to_append, ignore_index=True)
/home/leib

variable  importance
1                 hours_week-4    0.011461
4                 hours_week-1    0.010682
5           hours_current_week    0.971659
86         Wind_avg_std_week-1    0.000863
89         Pres_avg_avg_week-1    0.003323
95   Temp_avg_avg_current_week    0.000231
113  Pres_min_min_current_week    0.001780

### Sudden errors
We have a suspicion that the model we just trained does a very simple classification task using the errors of the last weeks, If the model finds errors in that weeks then it predicts an error in the following 4 weeks because it is normal to have errors recurrent errors.

From now on we will denote this errors as **"easy errors"**. This kind of error is easy to predict and we are more interested in predicting the from now on denoted **"sudden errors"**. This kind of errors are errors that appear without having a hard history of errors in the past weeks.

For example an error of type sudden whould be a lampost that suffers and error but we have all the variables hors_week-i at 0 or even one of them >0.

We will define an error as sudden error if we have 2 or less past weeks with errors. We consider the variable current_week to be a past week.

The first step will be to extract this kind of errors from the test data and see how the model we just trained predicts them to verify our theory

In [9]:
test_sudden, test_easy = split_easy_and_sudden_errors(test)

x_test_sudden, y_test_sudden = split_x_y(test_sudden, cols_to_train)
x_test_easy, y_test_easy = split_x_y(test_easy, cols_to_train)

Let's apply the model "ada_model" to the splited test dataset to verify our theory:

In [10]:
test_model(ada_model, x_test_sudden, y_test_sudden, 0.45)

{'total_accuracy': 0.23160644318676535,
 'yes_accuracy': 0.23160644318676535,
 'no_accuracy': None}

In [11]:
test_model(ada_model, x_test_easy, y_test_easy, 0.45)

{'total_accuracy': 0.991163406659088,
 'yes_accuracy': 0.9919265033407573,
 'no_accuracy': 0.9910088924590257}

We can see that the model almost has a perfect fit with the test_easy dataset. On the other hand, it has very bad performance on the test_sudden dataset. We can not consider ada_model to be the optimal predictor because it has a limited capacity of detecting sudden errors. We will have to design a better model for this cases.

To do it, the best way will be to split the datasets train, validation and test to train the sub-model so we make sure that the models are trained with the same datasests or subdatasets.

In [12]:
train_sudden, train_easy = split_easy_and_sudden_errors(train)
validation_sudden, validation_easy = split_easy_and_sudden_errors(validation)

# The dataset train_sudden has just rows with the column "error_next_four_weeks" = "Yes" so we will have to add
# some "No" rows in order to the model to train. To do this we will simply add a random sample of length len(train_sudden)
# of "No" rows to the dataset train_sudden.
train_sudden = pd.concat(
    [
        train.loc[train["error_next_four_weeks"] == "No"].sample(len(train_sudden)),
        train_sudden
    ],
    sort=True
).sample(frac=1.0, random_state=42)

validation_sudden = pd.concat(
    [
        validation.loc[validation["error_next_four_weeks"] == "No"].sample(len(validation_sudden)),
        validation_sudden
    ],
    sort=True
).sample(frac=1.0, random_state=42)

x_train_sudden, y_train_sudden = split_x_y(train_sudden, cols_to_train)
x_validation_sudden, y_validation_sudden = split_x_y(validation_sudden, cols_to_train)

In [13]:
# Train the model:
model_sudden_results = evaluate_models(
    max_depth_l = [1, 2, 3, 4],
    n_estimators_l = [1, 5, 10, 30, 100, 200, 300],
    lr_l = [0.05, 0.1, 0.2, 0.5, 0.7],
    prob_threshold_l = np.arange(0.40, 0.60, 0.01).tolist(),
    x_train = x_train_sudden,
    y_train = y_train_sudden,
    x_validation = x_validation_sudden,
    y_validation = y_validation_sudden
)

/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/ensemble/_base.py:166: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/home/leibniz/Desktop/IHMAN/predictive_maintenance/training_functions/training_functions.py:162: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  model_results = model_results.append(row_to_append, ignore_index=True)
/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expec

In [27]:
model_sudden_results.loc[(model_sudden_results["no_accuracy"] >= model_sudden_results["no_accuracy"].max()-0.37) & (model_sudden_results["yes_accuracy"] >= model_sudden_results["yes_accuracy"].max()-0.37)]

learning_rate  n_estimators  total_accuracy  yes_accuracy  no_accuracy  \
1075            0.5           5.0        0.645814      0.656085     0.635543   
1076            0.5           5.0        0.644880      0.653595     0.636166   
1077            0.5           5.0        0.644880      0.653595     0.636166   
1078            0.5           5.0        0.644880      0.653595     0.636166   
1079            0.5           5.0        0.644880      0.653595     0.636166   
2090            0.7          10.0        0.640056      0.641457     0.638655   
2091            0.7          10.0        0.643013      0.638967     0.647059   
2133            0.1          30.0        0.651883      0.661064     0.642702   
2151            0.2          30.0        0.645347      0.656396     0.634298   
2152            0.2          30.0        0.653439      0.631186     0.675692   
2189            0.7          30.0        0.642546      0.643946     0.641145   

      prob_threshold  tree_depth  
1075            0.55         2.0  
1076            0.56         2.0  
1077            0.57         2.0  
1078            0.58         2.0  
1079            0.59         2.0  
2090            0.50         3.0  
2091            0.51         3.0  
2133            0.53         3.0  
2151            0.51         3.0  
2152            0.52         3.0  
2189            0.49         3.0

In [31]:
ada_sudden_model = train_ada_boost(
    max_depth_tree = 3,
    n_estimators = 10,
    lr = 0.7,
    x  = x_train_sudden,
    y = y_train_sudden
)
# Test:
test_model(
    model = ada_sudden_model, 
    x = x_test_sudden, 
    y = y_test_sudden,
    prob_threshold = 0.5
)

/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/home/leibniz/anaconda3/envs/predic_maint/lib/python3.11/site-packages/sklearn/ensemble/_base.py:166: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(


{'total_accuracy': 0.5006530256856769,
 'yes_accuracy': 0.5006530256856769,
 'no_accuracy': None}

We managed to double our accuracy with this model on the sudden errors. Let's check the accuracy now for the whole test dataset:

In [32]:
# Test:
test_model(
    model = ada_sudden_model,
    x = x_test, 
    y = y_test,
    prob_threshold = 0.5
)

{'total_accuracy': 0.6142723454761253,
 'yes_accuracy': 0.8634863486348635,
 'no_accuracy': 0.5557434574895362}

In [15]:
# Save the dataframes of the models!!!!!
model_results.to_csv("model_results.csv")
model_sudden_results.to_csv("model_sudden_results.csv")

In [33]:
# Check of the importance of the variables:
feature_importances = variable_importance(
    ada_model = ada_sudden_model,
    trained_columns = cols_to_train
)
feature_importances.loc[feature_importances["importance"] != 0]

/home/leibniz/Desktop/IHMAN/predictive_maintenance/test_evaluate_functions/test_evaluate_functions.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  variable_importance_df = variable_importance_df.append(row_to_append, ignore_index=True)
/home/leibniz/Desktop/IHMAN/predictive_maintenance/test_evaluate_functions/test_evaluate_functions.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  variable_importance_df = variable_importance_df.append(row_to_append, ignore_index=True)
/home/leibniz/Desktop/IHMAN/predictive_maintenance/test_evaluate_functions/test_evaluate_functions.py:32: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  variable_importance_df = variable_importance_df.append(row_to_append, ignore_index=True)
/home/leib

variable  importance
0                   Unnamed: 0    0.161663
1                 hours_week-4    0.028793
2                 hours_week-3    0.007584
3                 hours_week-2    0.057319
4                 hours_week-1    0.022166
5           hours_current_week    0.044024
7          Temp_avg_avg_week-4    0.020343
8          Temp_avg_std_week-4    0.041815
9          Temp_min_min_week-4    0.044585
14          Hum_max_max_week-4    0.020425
16          Hum_avg_std_week-4    0.036039
20         Wind_avg_std_week-4    0.025877
23         Pres_avg_avg_week-4    0.037437
30         Temp_avg_std_week-3    0.041470
34          Dew_avg_std_week-3    0.027739
42         Wind_avg_std_week-3    0.017136
46         Pres_avg_std_week-3    0.003222
54          Dew_max_max_week-2    0.004713
57          Dew_min_min_week-2    0.012199
64         Wind_avg_std_week-2    0.012503
74         Temp_avg_std_week-1    0.017438
75         Temp_min_min_week-1    0.005954
77          Dew_avg_avg_week-1    0.007127
78          Dew_avg_std_week-1    0.021223
85         Wind_avg_avg_week-1    0.016572
88         Pres_max_max_week-1    0.062291
90         Pres_avg_std_week-1    0.024425
91         Pres_min_min_week-1    0.016955
96   Temp_avg_std_current_week    0.000636
99    Dew_avg_avg_current_week    0.024490
101   Dew_min_min_current_week    0.011873
104   Hum_avg_std_current_week    0.042738
105   Hum_min_min_current_week    0.015142
107  Wind_avg_avg_current_week    0.022429
111  Pres_avg_avg_current_week    0.019998
113  Pres_min_min_current_week    0.023653

In [34]:
x_train

Unnamed: 0  hours_week-4  hours_week-3  hours_week-2  hours_week-1  \
211529       89396           0.0           0.0           0.0           0.0   
267433      145300           0.0           0.0           0.0           0.0   
201060       78927           0.0           0.0           0.0           0.0   
22576        22576           0.0           0.0           0.0           0.0   
121602       25462           0.0           0.0           0.0           0.0   
...            ...           ...           ...           ...           ...   
274842      152709           0.0           0.0           0.0           0.0   
291150      169017           0.0           0.0           0.0           0.0   
263562      141429           0.0           0.0           0.0           0.0   
311529      189396           0.0           0.0           0.0           0.0   
294677      172544           0.0           0.0           0.0           0.0   

        hours_current_week  Temp_max_max_week-4  Temp_avg_avg_week-4  \
211529                 0.0            16.111111             7.206349   
267433                 0.0            36.111111            25.809524   
201060                 0.0            17.777778             8.484127   
22576                  0.0            18.888889            13.650794   
121602                 0.0            30.000000            25.595238   
...                    ...                  ...                  ...   
274842                 0.0            25.941402            17.150754   
291150                 0.0            22.777778            14.142857   
263562                 0.0            27.777778            16.952381   
311529                 0.0            32.222222            20.960317   
294677                 0.0            17.777778             6.404762   

        Temp_avg_std_week-4  Temp_min_min_week-4  ...  \
211529             1.136612             0.000000  ...   
267433             2.065755            16.111111  ...   
201060             2.009421            -1.111111  ...   
22576              1.678267             6.111111  ...   
121602             0.477599            20.000000  ...   
...                     ...                  ...  ...   
274842             1.734109             8.732860  ...   
291150             2.399386             3.888889  ...   
263562             3.796445             5.000000  ...   
311529             3.014661            11.111111  ...   
294677             1.667196            -3.888889  ...   

        Wind_max_max_current_week  Wind_avg_avg_current_week  \
211529                  22.000000                   6.042857   
267433                  21.000000                   4.900000   
201060                  20.000000                   3.242857   
22576                   20.000000                   7.728571   
121602                  14.000000                   6.542857   
...                           ...                        ...   
274842                  20.740935                   6.934186   
291150                  10.000000                   2.585714   
263562                  21.000000                   5.171429   
311529                  18.000000                   6.885714   
294677                  18.000000                   5.514286   

        Wind_avg_std_current_week  Wind_min_min_current_week  \
211529                   2.984324                   0.000000   
267433                   1.188837                   0.000000   
201060                   1.729024                   0.000000   
22576                    2.023787                   0.000000   
121602                   0.541163                   0.000000   
...                           ...                        ...   
274842                   2.325505                   0.024012   
291150                   0.569879                   0.000000   
263562                   1.207910                   0.000000   
311529                   1.404076                   0.000000   
294677                   2.007842               

15295

In [ ]:
{'illora': ('2022-12-01', '2023-01-01'), 'canyelles': ('2022-12-01', '2023-01-01'), 'mejorada': ('2022-12-01', '2023-01-01')}